EMAIL  KDC SRCHWRD        DATE
0      mkh0813@naver.com    2     NaN  2023-06-23
2  dilicat0813@naver.com    6     미술사  2023-06-23
3  lazycat0813@gmail.com    3   사회 과학  2023-06-23

In [1]:
import pandas as pd
import re
import os

folder_path = r"C:\RPA\Library\Data"

# 폴더가 존재하지 않으면 폴더를 생성합니다
if not os.path.exists(folder_path):
    os.makedirs(folder_path)

file_path = os.path.join(folder_path, "subscribe.csv")

#기본 DB불러오기
total = pd.read_csv("data/total.csv", index_col=0) #경로/이름 설정
subscribe = pd.read_csv("data/subscribe.csv") #경로/이름 설정
subscribe.drop_duplicates(subset="EMAIL", keep='last', inplace=True)
subscribe.to_csv(file_path, index=False, encoding='utf-8-sig') #RPA 소스 파일 저장 #논리상 위치 여기가 맞음
DT_Query = total[(total['MUMM_LON_HALFLIFE_CO'] >= 350) & (total['MUMM_LON_HALFLIFE_CO'] <= 6000)] #반감기 데이터 중 이상치 및 상위 5퍼센트 제거
DT_Query = DT_Query[(DT_Query['LON_CO'] <= 6500)] #누적 대출수 상위 5퍼센트 제거

DT_recommend = pd.DataFrame()

for index, row in subscribe.iterrows():
    kdc_query = row['KDC']
    srchwrd_query = row['SRCHWRD']
    file_name = row['EMAIL']
    DT_Query1 = DT_Query[DT_Query['KDC_1'] == kdc_query]

    srchwrd = srchwrd_query
    
    try:
        srchwrd_list = re.findall(r'\w+', srchwrd)
    except:
        srchwrd_list = []
    
    if srchwrd:
        DT_Query2 = DT_Query1[
            DT_Query1['TITLE_NM'].str.contains('|'.join(srchwrd_list), regex=True) |
            DT_Query1['AUTHR_NM'].str.contains('|'.join(srchwrd_list), regex=True) |
            DT_Query1['PUBLISHER_NM'].str.contains('|'.join(srchwrd_list), regex=True) |
            DT_Query1['BOOK_INTRCN_CN'].str.contains('|'.join(srchwrd_list), regex=True) |
            DT_Query1['Combined'].str.contains('|'.join(srchwrd_list), regex=True)
        ]
        DT_Query2 = DT_Query2.drop_duplicates()
    
        if len(DT_Query2) > 0:
            DT_recommend = DT_Query2.sample(5)
        else:
            DT_recommend = DT_Query1.sample(5)
    else:
        DT_recommend = DT_Query1.sample(5)

    DT_recommend.drop(columns=['BOOK_MASTR_SEQ_NO', 'MUMM_LON_HALFLIFE_CO', 'MXMM_LON_HALFLIFE_CO', 'AVRG_LON_HALFLIFE_CO', 'BOOK_CO','ISBN_THIRTEEN_NO','SEQ_NO','ADTION_SMBL_NM','LON_CO','Combined', 'KDC_1', 'KDC_12', 'KDC_123'],axis=1, inplace=True)
    
    file_path = os.path.join(folder_path, f"{file_name}.csv")
    DT_recommend.to_csv(file_path, index=False, encoding='utf -8-sig') #RPA 소스 파일 저장
    


C:\Users\mkh08\AppData\Local\Temp\ipykernel_21816\1808820258.py:14: DtypeWarning: Columns (12,15,18,19,20) have mixed types. Specify dtype option on import or set low_memory=False.
  total = pd.read_csv("data/total.csv", index_col=0) #경로/이름 설정


In [34]:
print(DT_recommend)

        BOOK_MASTR_SEQ_NO        ISBN_NO  MUMM_LON_HALFLIFE_CO  \
256621            2102515  9788995748787                   954   
523821            5470816  9788925567518                   100   
27188              279974  9788974600891                  1212   
82599              683187  9788930620918                  2060   
181824            1529462  9788935653096                  4636   

        MXMM_LON_HALFLIFE_CO  AVRG_LON_HALFLIFE_CO  BOOK_CO  ISBN_THIRTEEN_NO  \
256621                  4469                  2791      106      9.788996e+12   
523821                   502                   379       22      9.788926e+12   
27188                   5791                  4182       36      9.788975e+12   
82599                   7656                  5153       14      9.788931e+12   
181824                  7375                  6627       17      9.788936e+12   

                                      TITLE_NM             AUTHR_NM  \
256621                           (아리스토텔레스) 수사

In [5]:
import plotly.express as px
import plotly.graph_objects as go


In [6]:
fig = px.histogram(total, x="LON_CO")
fig.update_layout(bargap=0.2)
fig.show()

In [15]:
df_ex = total[(total["LON_CO"] > 10000)]

In [25]:
len(total)


532952

In [31]:
len(total[(total["MUMM_LON_HALFLIFE_CO"] > 6000)])

27410